## 나라별 언어 예측
- 중국어 & 일본어 & 대만어(아직 데이터 못찾음)

In [1]:
# 모듈로딩
import pandas as pd
import openpyxl
import jieba
import jieba.posseg as pseg
import torch



In [2]:
# file 불러오기
file = 'data/Chinese-tok.xlsx'

In [3]:
chinaDF = pd.read_excel(file)
chinaDF.head()

version  version2     h.title                                     respType  \
0        4         2  Bible(CHI)  Constructed in accordance to CES standards.   
1        4         2  Bible(CHI)  Constructed in accordance to CES standards.   
2        4         2  Bible(CHI)  Constructed in accordance to CES standards.   
3        4         2  Bible(CHI)  Constructed in accordance to CES standards.   
4        4         2  Bible(CHI)  Constructed in accordance to CES standards.   

                      respName  wordCount  byteCount  units     distributor  \
0  Christos Christodoulopoulos     677919    5428802  bytes  Bible Database   
1  Christos Christodoulopoulos     677919    5428802  bytes  Bible Database   
2  Christos Christodoulopoulos     677919    5428802  bytes  Bible Database   
3  Christos Christodoulopoulos     677919    5428802  bytes  Bible Database   
4  Christos Christodoulopoulos     677919    5428802  bytes  Bible Database   

                   eAddress  ...    id3    id4 lang    id5  type      id6  \
0  http://bibledatabase.com  ...  utf-8  Bible   zh  b.GEN  book  b.GEN.1   
1  http://bibledatabase.com  ...  utf-8  Bible   zh  b.GEN  book  b.GEN.1   
2  http://bibledatabase.com  ...  utf-8  Bible   zh  b.GEN  book  b.GEN.1   
3  http://bibledatabase.com  ...  utf-8  Bible   zh  b.GEN  book  b.GEN.1   
4  http://bibledatabase.com  ...  utf-8  Bible   zh  b.GEN  book  b.GEN.1   

     type7                                  seg        id8  type9  
0  chapter                           起初 神 創造 天地  b.GEN.1.1  verse  
1  chapter     地是 空虛 混沌 ． 淵面 黑暗 ． 神 的 靈運 行在 水面上  b.GEN.1.2  verse  
2  chapter                 神說 、 要 有 光 、 就 有 了 光  b.GEN.1.3  verse  
3  chapter             神 看 光是 好 的 、 就 把 光 暗 分開了  b.GEN.1.4  verse  
4  chapter  神稱光為晝 、 稱暗為夜 ． 有 晚上 、 有 早晨 、 這是 頭一日  b.GEN.1.5  verse  

[5 rows x 32 columns]

In [4]:
# seg 컬럼 제외하고 나머지 다 지우기
chinaDF=chinaDF[['seg']]
chinaDF

seg
0                                             起初 神 創造 天地
1                       地是 空虛 混沌 ． 淵面 黑暗 ． 神 的 靈運 行在 水面上
2                                   神說 、 要 有 光 、 就 有 了 光
3                               神 看 光是 好 的 、 就 把 光 暗 分開了
4                    神稱光為晝 、 稱暗為夜 ． 有 晚上 、 有 早晨 、 這是 頭一日
...                                                  ...
31096  聖靈 和 新婦 都 說來 。 聽見 的 人 也 該說來 。 口渴 的 人 也 當來 ． 願意...
31097  我 向 一切 聽見這書 上 豫 言 的 作見證 、 若 有 人 在 這豫 言 上 加添 甚 ...
31098  這書 上 的 豫言 、 若 有 人 刪 去 甚麼 、 神必從這書 上 所 寫 的 生命樹 、...
31099       證明 這事 的 說 、 是 了 ． 我 必 快來 。 阿們 。 主耶 穌阿 、 我願你來
31100                        願主 耶穌 的 恩惠 、 常與眾 聖徒 同在 。 阿們

[31101 rows x 1 columns]

In [5]:
text = '起初 神 創造 天地'
words = pseg.cut(text)
for w in words:
    print(f'{w.word} = {w.flag}')

Building prefix dict from the default dictionary ...
Loading model from cache C:\Users\User\AppData\Local\Temp\jieba.cache
Loading model cost 0.779 seconds.
Prefix dict has been built successfully.


起初 = d
  = x
神 = n
  = x
創造 = v
  = x
天地 = n


In [6]:
# 점이랑 쉼표 제거하기
import re
import pandas as pd
chinaDF['seg'] = chinaDF['seg'].apply(lambda x: re.sub(r'[。 、 ．]', '', str(x)))
print(chinaDF['seg'])


0                                            起初神創造天地
1                                地是空虛混沌淵面黑暗神的靈運行在水面上
2                                          神說要有光就有了光
3                                      神看光是好的就把光暗分開了
4                               神稱光為晝稱暗為夜有晚上有早晨這是頭一日
                            ...                     
31096          聖靈和新婦都說來聽見的人也該說來口渴的人也當來願意的都可以白白取生命的水喝
31097    我向一切聽見這書上豫言的作見證若有人在這豫言上加添甚麼神必將寫在這書上的災禍加在他身上
31098              這書上的豫言若有人刪去甚麼神必從這書上所寫的生命樹和聖城刪去他的分
31099                         證明這事的說是了我必快來阿們主耶穌阿我願你來
31100                               願主耶穌的恩惠常與眾聖徒同在阿們
Name: seg, Length: 31101, dtype: object


In [7]:
chinaDF

seg
0                                          起初神創造天地
1                              地是空虛混沌淵面黑暗神的靈運行在水面上
2                                        神說要有光就有了光
3                                    神看光是好的就把光暗分開了
4                             神稱光為晝稱暗為夜有晚上有早晨這是頭一日
...                                            ...
31096        聖靈和新婦都說來聽見的人也該說來口渴的人也當來願意的都可以白白取生命的水喝
31097  我向一切聽見這書上豫言的作見證若有人在這豫言上加添甚麼神必將寫在這書上的災禍加在他身上
31098            這書上的豫言若有人刪去甚麼神必從這書上所寫的生命樹和聖城刪去他的分
31099                       證明這事的說是了我必快來阿們主耶穌阿我願你來
31100                             願主耶穌的恩惠常與眾聖徒同在阿們

[31101 rows x 1 columns]

# 타이완 DF 만들고 전처리

In [8]:
# file 불러오기
file = 'data/taiwan02.xlsx'
TaiwanDF = pd.read_excel(file)
TaiwanDF

id conversations  \
0                     NaN          from   
1                 baize_0         human   
2                     NaN           gpt   
3                 baize_1         human   
4                     NaN           gpt   
...                   ...           ...   
46538          baize_2029           NaN   
46539                 NaN           NaN   
46540          baize_2047           NaN   
46541                 NaN           NaN   
46542  self_instruct_2215           NaN   

                                              Unnamed: 2  
0                                                  value  
1                                          給我三個保持健康的小撇步。  
2      1.飲食要均衡，多攝取水果和蔬菜。\n2.定期運動，保持身體活躍和強壯。\n3.保持充足的睡...  
3                                                三原色是什麼？  
4                                          三原色是紅色、藍色和黃色。  
...                                                  ...  
46538                                                NaN  
46539                                                NaN  
46540                                                NaN  
46541                                                NaN  
46542                                                NaN  

[46543 rows x 3 columns]

In [9]:


# "Unnamed"이라는 컬럼 이름을 변경하고자 하는 이름으로 설정
new_column_name = "seg"

# 컬럼 이름 변경
TaiwanDF = TaiwanDF.rename(columns={"Unnamed: 2": new_column_name})

print("컬럼 이름을 변경한 DataFrame:")
TaiwanDF

컬럼 이름을 변경한 DataFrame:


id conversations  \
0                     NaN          from   
1                 baize_0         human   
2                     NaN           gpt   
3                 baize_1         human   
4                     NaN           gpt   
...                   ...           ...   
46538          baize_2029           NaN   
46539                 NaN           NaN   
46540          baize_2047           NaN   
46541                 NaN           NaN   
46542  self_instruct_2215           NaN   

                                                     seg  
0                                                  value  
1                                          給我三個保持健康的小撇步。  
2      1.飲食要均衡，多攝取水果和蔬菜。\n2.定期運動，保持身體活躍和強壯。\n3.保持充足的睡...  
3                                                三原色是什麼？  
4                                          三原色是紅色、藍色和黃色。  
...                                                  ...  
46538                                                NaN  
46539                                                NaN  
46540                                                NaN  
46541                                                NaN  
46542                                                NaN  

[46543 rows x 3 columns]

In [10]:
TaiwanDF = TaiwanDF[['seg']]
TaiwanDF

seg
0                                                  value
1                                          給我三個保持健康的小撇步。
2      1.飲食要均衡，多攝取水果和蔬菜。\n2.定期運動，保持身體活躍和強壯。\n3.保持充足的睡...
3                                                三原色是什麼？
4                                          三原色是紅色、藍色和黃色。
...                                                  ...
46538                                                NaN
46539                                                NaN
46540                                                NaN
46541                                                NaN
46542                                                NaN

[46543 rows x 1 columns]

In [11]:
TaiwanDF = TaiwanDF.dropna()
TaiwanDF

seg
0                                                  value
1                                          給我三個保持健康的小撇步。
2      1.飲食要均衡，多攝取水果和蔬菜。\n2.定期運動，保持身體活躍和強壯。\n3.保持充足的睡...
3                                                三原色是什麼？
4                                          三原色是紅色、藍色和黃色。
...                                                  ...
46528                             選擇我們的環保可重複使用袋子，一起走向綠色！
46529                          以更好的英文風格重寫以下句子這是有史以來最棒的事情
46530                                       這是有史以來最棒的事情！
46531                              請回答這個問題.指示全世界有多少人精通回答
46532                                 全世界大約有800萬個精通的開發者。

[46421 rows x 1 columns]

In [12]:
# 문장부호들 제거함
import re
import pandas as pd
TaiwanDF['seg'] = TaiwanDF['seg'].apply(lambda x: re.sub(r'[。 、「 」 , << >> % [] 《》 : ! ， -] ', '', str(x)))
print(TaiwanDF['seg'])

0                                                    value
1                                            給我三個保持健康的小撇步。
2        1.飲食要均衡，多攝取水果和蔬菜。\n2.定期運動，保持身體活躍和強壯。\n3.保持充足的睡...
3                                                  三原色是什麼？
4                                            三原色是紅色、藍色和黃色。
                               ...                        
46528                               選擇我們的環保可重複使用袋子，一起走向綠色！
46529                            以更好的英文風格重寫以下句子這是有史以來最棒的事情
46530                                         這是有史以來最棒的事情！
46531                                請回答這個問題.指示全世界有多少人精通回答
46532                                   全世界大約有800萬個精通的開發者。
Name: seg, Length: 46421, dtype: object


C:\Users\User\AppData\Local\Temp\ipykernel_10972\867817834.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  TaiwanDF['seg'] = TaiwanDF['seg'].apply(lambda x: re.sub(r'[。 、「 」 , << >> % [] 《》 : ! ， -] ', '', str(x)))


In [13]:
TaiwanDF

seg
0                                                  value
1                                          給我三個保持健康的小撇步。
2      1.飲食要均衡，多攝取水果和蔬菜。\n2.定期運動，保持身體活躍和強壯。\n3.保持充足的睡...
3                                                三原色是什麼？
4                                          三原色是紅色、藍色和黃色。
...                                                  ...
46528                             選擇我們的環保可重複使用袋子，一起走向綠色！
46529                          以更好的英文風格重寫以下句子這是有史以來最棒的事情
46530                                       這是有史以來最棒的事情！
46531                              請回答這個問題.指示全世界有多少人精通回答
46532                                 全世界大約有800萬個精通的開發者。

[46421 rows x 1 columns]

In [14]:
# 중국어 번체자를 제외한 행 제거거
TaiwanDF['seg'] = TaiwanDF['seg'].str.replace(r'[^\u4e00-\u9fff]+', '', regex=True)

print("중국어 번체자만 남기고 문장부호를 제거한 DataFrame:")
print(TaiwanDF)

중국어 번체자만 남기고 문장부호를 제거한 DataFrame:
                                                  seg
0                                                    
1                                        給我三個保持健康的小撇步
2      飲食要均衡多攝取水果和蔬菜定期運動保持身體活躍和強壯保持充足的睡眠並保持一個固定的睡眠時間表
3                                              三原色是什麼
4                                         三原色是紅色藍色和黃色
...                                               ...
46528                            選擇我們的環保可重複使用袋子一起走向綠色
46529                       以更好的英文風格重寫以下句子這是有史以來最棒的事情
46530                                     這是有史以來最棒的事情
46531                            請回答這個問題指示全世界有多少人精通回答
46532                                  全世界大約有萬個精通的開發者

[46421 rows x 1 columns]


C:\Users\User\AppData\Local\Temp\ipykernel_10972\115402806.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  TaiwanDF['seg'] = TaiwanDF['seg'].str.replace(r'[^\u4e00-\u9fff]+', '', regex=True)


In [15]:
TaiwanDF

seg
0                                                    
1                                        給我三個保持健康的小撇步
2      飲食要均衡多攝取水果和蔬菜定期運動保持身體活躍和強壯保持充足的睡眠並保持一個固定的睡眠時間表
3                                              三原色是什麼
4                                         三原色是紅色藍色和黃色
...                                               ...
46528                            選擇我們的環保可重複使用袋子一起走向綠色
46529                       以更好的英文風格重寫以下句子這是有史以來最棒的事情
46530                                     這是有史以來最棒的事情
46531                            請回答這個問題指示全世界有多少人精通回答
46532                                  全世界大約有萬個精通的開發者

[46421 rows x 1 columns]

In [16]:
# # 중국어 문장 토큰화 함수
# def tokenize_chinese(text):
#     return jieba.lcut(text)

# # 각 텍스트에 대해 토큰화 수행
# TaiwanDF['seg'] = TaiwanDF['seg'].apply(tokenize_chinese)

# print(TaiwanDF['seg'])

In [17]:
# 각 데이터프레임에 라벨을 추가하기 위한 새로운 컬럼 생성
chinaDF['label'] = 0
TaiwanDF['label'] = 1

# 두 개의 데이터프레임을 하나로 합치기
AsiaDF = pd.concat([chinaDF,TaiwanDF], ignore_index=True)

print(AsiaDF)

                             seg  label
0                        起初神創造天地      0
1            地是空虛混沌淵面黑暗神的靈運行在水面上      0
2                      神說要有光就有了光      0
3                  神看光是好的就把光暗分開了      0
4           神稱光為晝稱暗為夜有晚上有早晨這是頭一日      0
...                          ...    ...
77517       選擇我們的環保可重複使用袋子一起走向綠色      1
77518  以更好的英文風格重寫以下句子這是有史以來最棒的事情      1
77519                這是有史以來最棒的事情      1
77520       請回答這個問題指示全世界有多少人精通回答      1
77521             全世界大約有萬個精通的開發者      1

[77522 rows x 2 columns]


C:\Users\User\AppData\Local\Temp\ipykernel_10972\680635676.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  TaiwanDF['label'] = 1


In [18]:
AsiaDF

seg  label
0                        起初神創造天地      0
1            地是空虛混沌淵面黑暗神的靈運行在水面上      0
2                      神說要有光就有了光      0
3                  神看光是好的就把光暗分開了      0
4           神稱光為晝稱暗為夜有晚上有早晨這是頭一日      0
...                          ...    ...
77517       選擇我們的環保可重複使用袋子一起走向綠色      1
77518  以更好的英文風格重寫以下句子這是有史以來最棒的事情      1
77519                這是有史以來最棒的事情      1
77520       請回答這個問題指示全世界有多少人精通回答      1
77521             全世界大約有萬個精通的開發者      1

[77522 rows x 2 columns]

In [19]:
vocab = {}
for idx in range(AsiaDF.shape[0]):
    result = jieba.cut(''.join(AsiaDF.iloc[idx][0])) # jieba는 morphs대신에 cut을 사용함

    for word in result:
        if len(word)>=2:
            if vocab.get(word):
                vocab[word] +=1
            else:
                vocab[word]=1

In [20]:
vocab

{'起初': 65,
 '創造': 753,
 '天地': 60,
 '地是': 3,
 '空虛': 16,
 '混沌': 7,
 '淵面': 2,
 '黑暗': 318,
 '靈運行': 1,
 '水面': 17,
 '神說': 23,
 '要有光': 2,
 '神看': 4,
 '光是': 8,
 '光暗': 1,
 '分開': 43,
 '神稱': 3,
 '光為': 2,
 '晝稱': 1,
 '暗為': 2,
 '夜有': 1,
 '晚上': 305,
 '早晨': 178,
 '這是頭': 2,
 '一日': 78,
 '諸水': 8,
 '之間': 1329,
 '有空': 7,
 '氣將': 1,
 '水分': 87,
 '上下': 19,
 '造出': 14,
 '空氣': 337,
 '將空氣': 2,
 '以下': 6114,
 '水空氣': 9,
 '以上': 168,
 '這樣': 1322,
 '天有': 2,
 '第二日': 9,
 '天下': 71,
 '水要': 4,
 '一處': 58,
 '旱地': 16,
 '露出': 36,
 '來事': 3,
 '稱水': 1,
 '聚處': 1,
 '海神': 1,
 '看著': 89,
 '地要': 24,
 '發生': 779,
 '青草': 14,
 '結種子': 3,
 '菜蔬': 20,
 '並結': 2,
 '果子': 180,
 '樹木': 107,
 '其類': 34,
 '包著': 4,
 '核事': 1,
 '核神': 1,
 '第三日': 30,
 '天上': 320,
 '可以': 8356,
 '分晝': 1,
 '夜作': 2,
 '記號定': 1,
 '節令': 3,
 '日子': 643,
 '並要': 98,
 '發光': 45,
 '天空': 271,
 '普照': 6,
 '地上': 576,
 '神造': 7,
 '兩個': 2440,
 '光大': 1,
 '管晝': 1,
 '管夜': 1,
 '造眾星': 1,
 '這些': 2644,
 '擺列': 8,
 '管理': 523,
 '夜分': 1,
 '明暗': 2,
 '第四日': 5,
 '多多': 31,
 '滋生': 13,
 '生命': 470,
 '物要': 3,
 '地面': 

In [21]:
sorted(vocab,key=lambda x : x[0], reverse=True)

['龜裂',
 '龐大而',
 '龐大',
 '龐巴迪爾',
 '龐培劇院',
 '龐溫',
 '龐大牆',
 '龐克和嘻哈',
 '龍子',
 '龍爭',
 '龍見',
 '龍向',
 '龍是',
 '龍威脅',
 '龍成',
 '龍的頭',
 '龍黃蜂',
 '龍並',
 '龍國王',
 '龍居高',
 '龍極',
 '龍頭',
 '龍鱗片',
 '龍龍',
 '龍聞',
 '龍蝦',
 '龍紋身',
 '齡大',
 '齡對',
 '齒數',
 '齒輪',
 '齒間',
 '齒目',
 '齐诺',
 '齋戒',
 '齊聲',
 '齊齊',
 '齊備',
 '齊全',
 '齊落',
 '齊公會',
 '齊心',
 '齊奧德羅西',
 '齊和合',
 '齊和替',
 '齊比納爾',
 '齊亞德',
 '齊射將',
 '齊聚',
 '齊驅',
 '齊平',
 '齊亞康妮',
 '齊康妮',
 '齊尼巴爾齊尼',
 '齊奧',
 '齊以',
 '齊為',
 '齊時',
 '齊輸入',
 '鼻孔',
 '鼻子',
 '鼻環',
 '鼻中',
 '鼻前',
 '鼻塞',
 '鼻水',
 '鼻腔',
 '鼴鼠',
 '鼴鼠屬',
 '鼴科',
 '鼴鼠定',
 '鼬鼠',
 '鼬花',
 '鼬子',
 '鼠標',
 '鼓眾',
 '鼓瑟',
 '鼓鈸',
 '鼓肚',
 '鼓勵',
 '鼓吹',
 '鼓彈琴',
 '鼓動',
 '鼓為',
 '鼓笛',
 '鼓舞人心',
 '鼓舞',
 '鼓掌',
 '鼓槌',
 '鼓手',
 '鼓起',
 '鼓勵員工',
 '鼓進行',
 '鼓現',
 '鼓旁',
 '鼓釀',
 '鼓洗',
 '鼓聲',
 '鼓螺絲',
 '鼎為',
 '黴菌',
 '黯然失色',
 '黨類',
 '黨裡',
 '黨之間',
 '黨制',
 '黨以',
 '黨派',
 '黨人絕',
 '黨人',
 '黨有',
 '黨人承認',
 '黨成員',
 '黨來',
 '黨通過',
 '黨承諾將',
 '黨獨',
 '黨能夠',
 '黨候',
 '黨還',
 '黨正',
 '黨上',
 '黨部長',
 '黨內閣',
 '黨並',
 '黨團',
 '黨然',
 '黨副候',
 '點燈',
 '點著',
 '點其',
 '點齊',
 '點出',
 '點餅',
 '點火'

In [22]:
len(vocab)

93949

In [23]:
trainDF = AsiaDF.sample(frac=0.9, random_state=42)
testDF = AsiaDF.drop(trainDF.index)

In [24]:
trainDF.shape, testDF.shape

((69770, 2), (7752, 2))

In [25]:
vocab

{'起初': 65,
 '創造': 753,
 '天地': 60,
 '地是': 3,
 '空虛': 16,
 '混沌': 7,
 '淵面': 2,
 '黑暗': 318,
 '靈運行': 1,
 '水面': 17,
 '神說': 23,
 '要有光': 2,
 '神看': 4,
 '光是': 8,
 '光暗': 1,
 '分開': 43,
 '神稱': 3,
 '光為': 2,
 '晝稱': 1,
 '暗為': 2,
 '夜有': 1,
 '晚上': 305,
 '早晨': 178,
 '這是頭': 2,
 '一日': 78,
 '諸水': 8,
 '之間': 1329,
 '有空': 7,
 '氣將': 1,
 '水分': 87,
 '上下': 19,
 '造出': 14,
 '空氣': 337,
 '將空氣': 2,
 '以下': 6114,
 '水空氣': 9,
 '以上': 168,
 '這樣': 1322,
 '天有': 2,
 '第二日': 9,
 '天下': 71,
 '水要': 4,
 '一處': 58,
 '旱地': 16,
 '露出': 36,
 '來事': 3,
 '稱水': 1,
 '聚處': 1,
 '海神': 1,
 '看著': 89,
 '地要': 24,
 '發生': 779,
 '青草': 14,
 '結種子': 3,
 '菜蔬': 20,
 '並結': 2,
 '果子': 180,
 '樹木': 107,
 '其類': 34,
 '包著': 4,
 '核事': 1,
 '核神': 1,
 '第三日': 30,
 '天上': 320,
 '可以': 8356,
 '分晝': 1,
 '夜作': 2,
 '記號定': 1,
 '節令': 3,
 '日子': 643,
 '並要': 98,
 '發光': 45,
 '天空': 271,
 '普照': 6,
 '地上': 576,
 '神造': 7,
 '兩個': 2440,
 '光大': 1,
 '管晝': 1,
 '管夜': 1,
 '造眾星': 1,
 '這些': 2644,
 '擺列': 8,
 '管理': 523,
 '夜分': 1,
 '明暗': 2,
 '第四日': 5,
 '多多': 31,
 '滋生': 13,
 '生命': 470,
 '物要': 3,
 '地面': 

In [26]:
trainDF.head()

seg  label
18938  那些分別為聖潔淨自己的進入園內跟在其中一個人的後頭喫豬肉和倉鼠並可憎之物他們必一同滅絕這是耶...      0
52877                    請列出哈利波特系列的所有書籍指示列出哈利波特系列的所有書籍回應      1
65775  以下是一個描述任務的指示並附帶提供更多背景的輸入請撰寫一個適當完成請求的回應指示撰寫一個表達...      1
33015  多攝取蛋白質蛋白質豐富的食物能夠提升新陳代謝因為消化蛋白質所需的能量比碳水化合物和脂肪多確保...      1
77384                              描述給定方法論背後的哲學輸入敏捷方法論輸出      1

In [27]:
train_text = trainDF['label']

In [31]:
trainDF.head()

seg  label
18938  那些分別為聖潔淨自己的進入園內跟在其中一個人的後頭喫豬肉和倉鼠並可憎之物他們必一同滅絕這是耶...      0
52877                    請列出哈利波特系列的所有書籍指示列出哈利波特系列的所有書籍回應      1
65775  以下是一個描述任務的指示並附帶提供更多背景的輸入請撰寫一個適當完成請求的回應指示撰寫一個表達...      1
33015  多攝取蛋白質蛋白質豐富的食物能夠提升新陳代謝因為消化蛋白質所需的能量比碳水化合物和脂肪多確保...      1
77384                              描述給定方法論背後的哲學輸入敏捷方法論輸出      1

In [35]:
from torch.utils.data import Dataset

class CustomDataset(Dataset):
    def __init__(self,table):
        self.table = table
        self.cat = self.table['label'].astype('category')
        self.label = self.cat.cat.codes
    
    def __len__(self):
        number = len(self.table)
        return number
    
    def __getitem__(self, idx):
        label = self.label.iloc[idx]
        sentence = self.table['seg'].iloc[idx]

        return label, sentence

In [37]:
import jieba
from torchtext.vocab import build_vocab_from_iterator

trainiter = CustomDataset(trainDF)

# 중국어 텍스트를 토큰화하는 함수 정의
# 이 함수 안에서 토큰화가 이루어져야함
def yield_tokens(train_iter):
    for _, text in train_iter:  # 레이블은 무시하고 텍스트만 사용 숫자, 텍스트 형태이기 때문에 _,text 이 순서로 적어줘야함
        text = str(text)  # 텍스트를 문자열로 변환
        yield jieba.lcut(text)  # jieba의 lcut 함수에 문자열 전달

# 단어 집합(vocabulary) 생성
vocab = build_vocab_from_iterator(yield_tokens(trainiter), min_freq=2, specials=['<PAD>', '<UNK>'])


In [38]:
vocab.set_default_index(vocab["<UNK>"])

In [39]:
jieba.lcut('我是韩国人')

['我', '是', '韩国', '人']

In [40]:
vocab(jieba.lcut('我是韩国人'))

[7, 4, 1, 12]

In [41]:
vocab(jieba.lcut('龍'))

[2321]

- 데이터 가공
    - 토큰 데이터 정수 인코딩
    - 데이터 길이 표준화

In [42]:
# 훈련용, 테스트용, 데이터셋으로 나누기
trainDF = AsiaDF.sample(frac=0.9, random_state=42)
testDF=AsiaDF.drop(trainDF.index)

In [43]:
trainDF.shape, testDF.shape

((69770, 2), (7752, 2))

In [44]:
import jieba

# 훈련 데이터와 테스트 데이터의 텍스트를 토큰화하여 리스트로 변환
train_tokens = [list(jieba.cut(text)) for text in trainDF['seg']]
test_tokens = [list(jieba.cut(text)) for text in testDF['seg']]


In [46]:
### 인코딩 : 문자 >>> 숫자로 변환
token_to_id = vocab.get_stoi()  # Dict

### 디코딩 : 숫자 >>> 문자로 변환
id_to_token = vocab.get_itos()  # List

In [47]:
### 단어를 정수로 변환 (단어/어휘 사전에 없는 문자는 <UNK>에 대응하는 숫자[1]로 처리)
UNK_ID = token_to_id["<UNK>"]   # 1
train_ids = [[token_to_id.get(token, UNK_ID) for token in text] for text in train_tokens]
test_ids = [[token_to_id.get(token, UNK_ID) for token in text] for text in test_tokens]

In [48]:
def add_padding(sequences, max_length, pad, start='R'):
    padded_sequences = []
    for sequence in sequences:
        if len(sequence) < max_length:
            padded_sequence = sequence + [0] * (max_length - len(sequence))
        else:
            padded_sequence = sequence[:max_length]
        padded_sequences.append(padded_sequence)
    return padded_sequences

In [49]:
# 패딩 추가
PAD_ID = token_to_id.get('<PAD>')
max_sequence_length = 50
train_ids = add_padding(train_ids, max_sequence_length,PAD_ID)
test_ids = add_padding(test_ids,max_sequence_length,PAD_ID)

In [50]:
print(f'[train_ids] -> {len(train_ids[1])}개')
print(f'[test_ids] -> {len(test_ids[1])}개')

[train_ids] -> 50개
[test_ids] -> 50개


In [51]:
print(train_ids[1])
print(test_ids[1])

[38, 265, 2810, 4057, 1318, 2, 87, 824, 68, 265, 2810, 4057, 1318, 2, 87, 824, 82, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[7631, 133, 367, 1354, 3049, 26, 129, 40200, 2, 7921, 5, 129, 3858, 52, 1, 13780, 2, 1277, 1, 6, 25, 168, 258, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]


In [52]:
from sklearn.preprocessing import LabelEncoder

# LabelEncoder 객체 생성
label_encoder = LabelEncoder()

# 문자열 Series를 숫자 Series로 변환
train_labels = label_encoder.fit_transform(trainDF['label'])
test_labels = label_encoder.fit_transform(testDF['label'])

In [53]:
label_encoder.classes_

array([0, 1], dtype=int64)

In [54]:
import torch
from torch.utils.data import TensorDataset, DataLoader

In [55]:
print(type(train_ids), type(trainDF.values))

<class 'list'> <class 'numpy.ndarray'>


In [56]:
dataDS1 = torch.LongTensor(train_ids)
labelDS1 = torch.LongTensor(train_labels)

dataDS2 = torch.LongTensor(test_ids)
labelDS2 = torch.LongTensor(test_labels)

print(dataDS1.shape, labelDS1.shape)
print(dataDS2.shape, labelDS2.shape)

torch.Size([69770, 50]) torch.Size([69770])
torch.Size([7752, 50]) torch.Size([7752])


In [57]:
# 데이터셋 생성
trainDS = TensorDataset(dataDS1, labelDS1)
testDS = TensorDataset(dataDS2, labelDS2)



In [58]:
# 데이터로더 생성
BATCH_SIZE = 32
trainDL = DataLoader(trainDS, BATCH_SIZE, shuffle=True)
testDL = DataLoader(testDS, BATCH_SIZE, shuffle=True)

In [59]:
for t,l in trainDL:
    print(t)
    print(l)
    print(t.shape, l.shape)
    break

tensor([[ 2095,    83,   226,  ...,     0,     0,     0],
        [  896,  1310,     3,  ...,     0,     0,     0],
        [    7,   212,     9,  ...,     0,     0,     0],
        ...,
        [   96,   150, 10904,  ...,     0,     0,     0],
        [   15,   388,  1193,  ...,     0,     0,     0],
        [ 4874,  3111,     1,  ...,     0,     0,     0]])
tensor([1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 0, 0, 0, 0, 1, 1, 1, 1, 0, 0, 1, 0, 1, 0,
        1, 1, 1, 0, 1, 0, 1, 0])
torch.Size([32, 50]) torch.Size([32])


In [60]:
train_text

18938    0
52877    1
65775    1
33015    1
77384    1
        ..
28876    0
56131    1
39419    1
4947     0
43220    1
Name: label, Length: 69770, dtype: int64

In [61]:
type(train_text)

pandas.core.series.Series

In [62]:
HIDDEN_SIZE = 3
EMBEDD_DIM = 40
VOCAB_SIZE = len(vocab)
NUM_CLASS = 2
EPOCHS = 10
LR = 5
BATCH_SIZE = 32
device=torch.device('cuda' if torch.cuda.is_available() else 'cpu')

In [63]:
import torch.nn as nn

### 모델 설계
### 입력층 : EmbeddingBag Layer - 레이어와 분류(classification) 목적을 위한 선형 레이어
### 은닉층 : Linear - 4개 클래스 분류
class TextModel(nn.Module):
    def __init__(self, VOCAB_SIZE, EMBEDD_DIM, HIDDEN_SIZE, NUM_CLASS):
        super().__init__()
        # 모델 구성 층 정의
        self.embedding = nn.Embedding(VOCAB_SIZE,EMBEDD_DIM,sparse=False,padding_idx=0)
        self.rnn = nn.LSTM(EMBEDD_DIM, HIDDEN_SIZE, 1, dropout=0, batch_first=True)
        self.fc = nn.Linear(HIDDEN_SIZE, NUM_CLASS)
        self.init_weights()
    
    # 가중치 초기화
    def init_weights(self):
        initrange = 0.5
        self.embedding.weight.data.uniform_(-initrange, initrange)
        self.fc.weight.data.uniform_(-initrange, initrange)
        self.fc.bias.data.zero_()

    # 순방향 학습 진행
    def forward(self, text):
        print('forward 들어가긴 했음')
        embedded = self.embedding(text)
        print("text ->", text)
        print("임베딩 -> ", embedded.shape)
        output, hidden = self.rnn(embedded)
        print(output.shape, hidden[-1].shape)
        result = self.fc(output[:,-1,:])
        print("result", result)
        
        return result

In [64]:
### 학습 관련 인스턴스
import torch.optim as optim
MODEL = TextModel(VOCAB_SIZE,EMBEDD_DIM,HIDDEN_SIZE,NUM_CLASS).to(device)
CRITERION = nn.CrossEntropyLoss()
OPTIMIZER = optim.SGD(MODEL.parameters(),lr=LR)
SCHEDULER = optim.lr_scheduler.StepLR(OPTIMIZER,step_size=1.0,gamma=0.1)
EPOCHS = 100

In [65]:

def train(model, dataloader, optimizer, criterion, epoch):
    
    model.train()
    
         
    total_acc, total_count = 0,0
    log_interval=100
    
    for idx, (text, label) in enumerate(dataloader):
        predicted_label = model(text)
        # predicted_label = predicted_label.squeeze(0)
        # print(predicted_label.shape, label.shape, "람벨")
        optimizer.zero_grad()
        loss = criterion(predicted_label, label)
        loss.backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), 0.1)
        optimizer.step()
        
        # 배치 학습 평가
        total_acc += (predicted_label.argmax(1) == label).sum().item()
        total_count += label.size(0)
        
        if idx % log_interval == 0 and idx > 0:
            pass
        print(f"epoch : {epoch} batch : {idx} loss : {loss.item()}")
        print(f"Accuracy : {total_acc/total_count}")
        total_acc, total_count = 0,0
            

In [66]:
train(MODEL,trainDL,OPTIMIZER,CRITERION,EPOCHS)

forward 들어가긴 했음
text -> tensor([[41345,  5936,  9647,  ...,     0,     0,     0],
        [ 3343,  1332,   150,  ...,     0,     0,     0],
        [   31,    10,     1,  ...,     0,     0,     0],
        ...,
        [21925, 41106,   669,  ...,     0,     0,     0],
        [   67,    39,    51,  ...,     0,     0,     0],
        [  185,   125, 13155,  ...,     0,     0,     0]])
임베딩 ->  torch.Size([32, 50, 40])
torch.Size([32, 50, 3]) torch.Size([1, 32, 3])
result tensor([[ 0.1910,  0.3302],
        [ 0.1910,  0.3302],
        [ 0.1910,  0.3302],
        [ 0.1910,  0.3302],
        [ 0.1910,  0.3302],
        [ 0.1910,  0.3302],
        [ 0.1910,  0.3302],
        [ 0.1910,  0.3302],
        [ 0.1910,  0.3301],
        [ 0.1910,  0.3302],
        [ 0.1910,  0.3302],
        [-0.1799, -0.3338],
        [ 0.1910,  0.3302],
        [-0.1268, -0.2345],
        [ 0.1910,  0.3302],
        [-0.0651, -0.1245],
        [-0.0977, -0.1969],
        [ 0.1910,  0.3302],
        [ 0.0162,  0.03

In [67]:
def text_pipeline(text):
   token=list(jieba.cut(text))
   
   indexes = vocab(token)
   print(indexes)
   train_ids = add_padding([indexes], max_sequence_length,PAD_ID)
   return train_ids        

In [68]:
def predict(model, text, text_pipeline):
    model.eval()  # 모델을 평가 상태로 설명

    indexes = text_pipeline(text)
    
    tensor = torch.tensor(indexes, dtype=torch.int64)
    
    with torch.no_grad():
        output = model(tensor)
        print(output)
        prediction = output.argmax(1).item()
        print(prediction)
    if prediction == 0:
        label = '중국어'
        
    elif prediction == 1:
        label = '대만어'
    else:
        label = '예측 불가'
    return label

In [87]:
new_data ="我去了学校"
#text_pipeline(new_data)

prediction = predict(MODEL, new_data,text_pipeline)
print("예측 결과:", prediction)

[7, 53, 10, 1]
forward 들어가긴 했음
text -> tensor([[ 7, 53, 10,  1,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
          0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
          0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0]])
임베딩 ->  torch.Size([1, 50, 40])
torch.Size([1, 50, 3]) torch.Size([1, 1, 3])
result tensor([[ 1.5152, -1.0358]])
tensor([[ 1.5152, -1.0358]])
0
예측 결과: 중국어


In [82]:
import torch
PATH = "./model/best_model.pt"
torch.save(MODEL.state_dict(),PATH)

In [73]:
# vocab을 pkl로 저장하기
import pickle

with open('model/vocab.pkl','wb') as f:
    pickle.dump(vocab,f)
